# Introduction

In order to train on the words in a legislative bill we want to make use of an existing Natural Language Processing (NLP) model in order to come up with a data structure that will encode contextual information.

To this end we use the BERT model, which is one of the modern NLP models that takes into account context.

For this project, we want to take the text from the bill and predict which party sponsored it

## First steps

Load the BERT model using pytorch.

Why pytorch, this is higher level libary for constructing machine learning models.

In [4]:
import fnmatch
import os.path

import pandas as pd
import transformers
from transformers import pipeline
import pandas as pd
import torch
import numpy as np
import json

In [5]:
from transformers import BertTokenizer, BertModel
tokenizer = BertTokenizer.from_pretrained('bert-base-cased')
model = BertModel.from_pretrained("bert-base-cased")

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertModel: ['cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Now that the we have the model, we want to run inference on the text and get the output token.

In [6]:
def generate_token(summary_json):
    """
    execute the BERT model on the title section of the summary
    :param summary_json: the data from a summary file
    :return: a numpy vector
    """
    text = summary_json['text']
    encoded_input = tokenizer(text, return_tensors='pt')
    print("encoded input")
    print(encoded_input)
    print("model output")
    output = model(**encoded_input)
#    print(type(output))
    last_shape = output.last_hidden_state.shape
    elements = np.cumproduct(last_shape)
    last_layer_vector = torch.from_numpy(output.last_hidden_state.detach().numpy().reshape(max(elements)))
#    print(type(last_layer_vector))
    return last_layer_vector

In [7]:
parent_path = os.path.dirname(os.getcwd())
search_path = os.path.join(parent_path, "data", "extracted")
token_path = os.path.join(parent_path, "data", "tokenized")

In [19]:
import pickle
for root, dirs, files in os.walk(search_path):
    for f in files:
        with open(os.path.join(root, f), 'r') as s_file:
            print(f'reading {f}')
            try:
                summary = json.load(s_file)
                encoding = generate_token(summary)get
                print(f'{len(encoding)} of type {type(encoding)}')
                summary["input_full"] = encoding
                df = pd.DataFrame(summary)
                output_path = os.path.join(token_path, f.replace(".json",".pkl"))
                print(f'saving {output_path}')
                df.to_pickle(output_path,compression="gzip",protocol=pickle.DEFAULT_PROTOCOL)
            except json.JSONDecodeError:
                with open("json_error.txt", 'a') as err_file:
                    err_file.write(s_file.name+"\n")
            except:
                with open("general_error.txt", 'a') as err_file:
                    err_file.write(s_file.name+"\n")




reading summary_bill_1811_1392983.json
encoded input
{'input_ids': tensor([[  101,   142,  8419,  1830, 27706,  8826,  1111,  5186,  2989,  8132,
           118, 18572,  1104,  6538,  2308,   119,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
model output
13056 of type <class 'torch.Tensor'>
saving C:\Users\benja\git-projects\bitbucket\nlp_legislation_prediction\data\tokenized\summary_bill_1811_1392983.pkl
reading summary_bill_1811_1392984.json
encoded input
{'input_ids': tensor([[  101, 11336, 26304,  1106,  1103,  5991,  4412,  1104, 14689,  1111,
          2436,   119,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
model output
9984 of type <class 'torch.Tensor'>
saving C:\Users\benja\git-projects\bitbucket\nlp_legislation_prediction\data\tokenized\summary_bil

These tensors all have different sizes, so running a cosine similarity will not work.
I will try to compress these down to a standard size.
Let's try this  : https://newbedev.com/downsample-a-1d-numpy-array

Let's reload and the dfs and save a resampled version of the encoding

In [12]:
import numpy as np
from scipy.signal import resample
from scipy.interpolate import interp1d

def ResampleLinear1D(original, targetLen):
    original = np.array(original, dtype=np.float)

    index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.float)
    index_floor = np.array(index_arr, dtype=np.int) #Round down

    index_ceil = index_floor + 1
    index_rem = index_arr - index_floor #Remain

    val1 = original[index_floor]
    val2 = original[index_ceil % len(original)]
    interp = val1 * (1.0-index_rem) + val2 * index_rem
    assert(len(interp) == targetLen)
    return interp

In [20]:
print(f'tokenized files are in {token_path}')
import fnmatch
for root,dirs, files in os.walk(token_path):
    for f in files:
        if not fnmatch.fnmatch(f, "*shrunk*"):
            pkl_file_path = os.path.join(root, f)
            print(f"processsing {f}")
            df = pd.read_pickle(pkl_file_path, compression="gzip")
    #        print(df)
            shrunk = ResampleLinear1D(df["input_full"], 2048)
    #        print(shrunk)
            # "status": 2, "party": 1
            df2 = pd.DataFrame({"status": df["status"][0:2048],
                                "party": df["party"][0:2048],
                                "input_shrunk": shrunk})
    #        print(df2.shape)
            df2.to_pickle(pkl_file_path.replace(".pkl","-shrunk.pkl"),compression="gzip", protocol=pickle.DEFAULT_PROTOCOL)

tokenized files are in C:\Users\benja\git-projects\bitbucket\nlp_legislation_prediction\data\tokenized
processsing summary_bill_1811_1392983.pkl
processsing summary_bill_1811_1392984.pkl
processsing summary_bill_1811_1392985.pkl
processsing summary_bill_1811_1392986.pkl
processsing summary_bill_1811_1392988.pkl
processsing summary_bill_1811_1392989.pkl
processsing summary_bill_1811_1392990.pkl
processsing summary_bill_1811_1392991.pkl
processsing summary_bill_1811_1392992.pkl
processsing summary_bill_1811_1392994.pkl
processsing summary_bill_1811_1392995.pkl
processsing summary_bill_1811_1392996.pkl
processsing summary_bill_1811_1392997.pkl
processsing summary_bill_1811_1393000.pkl
processsing summary_bill_1811_1393001.pkl
processsing summary_bill_1811_1393002.pkl
processsing summary_bill_1811_1393003.pkl
processsing summary_bill_1811_1393005.pkl
processsing summary_bill_1811_1393007.pkl
processsing summary_bill_1811_1393008.pkl
processsing summary_bill_1811_1393009.pkl
processsing sum

C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1811_1393019.pkl
processsing summary_bill_1811_1393020.pkl
processsing summary_bill_1811_1393021.pkl
processsing summary_bill_1811_1393022.pkl
processsing summary_bill_1811_1393023.pkl
processsing summary_bill_1811_1393024.pkl
processsing summary_bill_1811_1393026.pkl
processsing summary_bill_1811_1393028.pkl
processsing summary_bill_1811_1393029.pkl
processsing summary_bill_1811_1393030.pkl
processsing summary_bill_1811_1393032.pkl
processsing summary_bill_1811_1393033.pkl
processsing summary_bill_1811_1393034.pkl
processsing summary_bill_1811_1393036.pkl
processsing summary_bill_1811_1393038.pkl
processsing summary_bill_1811_1393039.pkl
processsing summary_bill_1811_1393040.pkl
processsing summary_bill_1811_1393041.pkl
processsing summary_bill_1811_1393042.pkl
processsing summary_bill_1811_1393044.pkl
processsing summary_bill_1811_1393045.pkl
processsing summary_bill_1811_1393046.pkl
processsing summary_bill_1811_1393047.pkl
processsing summary_bill_1811_1393

C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1811_1393054.pkl
processsing summary_bill_1811_1393055.pkl
processsing summary_bill_1811_1393057.pkl
processsing summary_bill_1811_1393058.pkl
processsing summary_bill_1811_1393059.pkl
processsing summary_bill_1811_1393060.pkl
processsing summary_bill_1811_1393061.pkl
processsing summary_bill_1811_1393063.pkl
processsing summary_bill_1811_1393064.pkl
processsing summary_bill_1811_1393065.pkl
processsing summary_bill_1811_1393066.pkl
processsing summary_bill_1811_1393067.pkl
processsing summary_bill_1811_1393068.pkl
processsing summary_bill_1811_1393071.pkl
processsing summary_bill_1811_1393072.pkl
processsing summary_bill_1811_1393074.pkl
processsing summary_bill_1811_1393076.pkl
processsing summary_bill_1811_1393077.pkl
processsing summary_bill_1811_1393078.pkl
processsing summary_bill_1811_1393079.pkl
processsing summary_bill_1811_1393080.pkl
processsing summary_bill_1811_1393082.pkl


...

C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1959_1546390.pkl
processsing summary_bill_1959_1546393.pkl
processsing summary_bill_1959_1546395.pkl
processsing summary_bill_1959_1546399.pkl
processsing summary_bill_1959_1546402.pkl
processsing summary_bill_1959_1546404.pkl
processsing summary_bill_1959_1546408.pkl
processsing summary_bill_1959_1546412.pkl
processsing summary_bill_1959_1546414.pkl
processsing summary_bill_1959_1546417.pkl
processsing summary_bill_1959_1546421.pkl
processsing summary_bill_1959_1546423.pkl
processsing summary_bill_1959_1546427.pkl
processsing summary_bill_1959_1546429.pkl
processsing summary_bill_1959_1546431.pkl
processsing summary_bill_1959_1546435.pkl
processsing summary_bill_1959_1546438.pkl
processsing summary_bill_1959_1546440.pkl
processsing summary_bill_1959_1546443.pkl
processsing summary_bill_1959_1546445.pkl
processsing summary_bill_1959_1546448.pkl
processsing summary_bill_1959_1546451.pkl
processsing summary_bill_1959_1546454.pkl
processsing summary_bill_1959_1546

C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl

processsing summary_bill_1959_1579963.pkl
processsing summary_bill_1959_1583495.pkl
processsing summary_bill_1959_1595686.pkl
processsing summary_bill_1959_1599982.pkl
processsing summary_bill_1959_1607568.pkl
processsing summary_bill_1959_1615421.pkl
processsing summary_bill_1959_1616153.pkl
processsing summary_bill_1959_1616154.pkl


C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  original = np.array(original, dtype=np.float)
C:\Users\benja\AppData\Local\Temp\ipykernel_38748\376862322.py:8: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  index_arr = np.linspace(0, len(original)-1, num=targetLen, dtype=np.fl